In [251]:
import plotly.express as px
import os

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

import CalculatedFieldSubroutines as cfs

import torch

import torch.nn as nn
from sklearn.model_selection import train_test_split

In [252]:
gmID = "3a2a78cc-db21-11ee-a158-97f8443fd730"

In [281]:
chassis_df = pd.read_csv(f"./data/chassis/{gmID}.csv")
best_pose_df = pd.read_csv(f"./data/best_pose/{gmID}.csv")

chassis_df = chassis_df.sort_values(by="time")
best_pose_df = best_pose_df.sort_values(by="time")

cfs.BinaryDrivingMode(chassis_df)
cfs.TernaryDrivingModeTransition(chassis_df)
cfs.LatLonTotalStdDev(best_pose_df)
cfs.ChassisBestPoseMatchedTime(chassis_df,best_pose_df)


merged_df = pd.merge(chassis_df,best_pose_df,on="ChassisBestPoseMatchedTime")

merged_df['time_sec'] = merged_df['time_x'].astype('datetime64[ns]')
merged_df['time_sec'] = merged_df['time_sec'].astype('datetime64[s]')

best_pose_df['time_sec'] = best_pose_df['time'].astype('datetime64[ns]')
best_pose_df['time_sec'] = best_pose_df['time_sec'].astype('datetime64[s]')

chassis_df['time_sec'] = chassis_df['time'].astype('datetime64[ns]')
chassis_df['time_sec'] = chassis_df['time_sec'].astype('datetime64[s]')

merged_df["drivingMode"] = np.where(merged_df["drivingMode"]  == "EMERGENCY_MODE", "COMPLETE_MANUAL",merged_df["drivingMode"])


merged_df


yawRate      drivingMode                   topic  msgsize  \
0            0  COMPLETE_MANUAL  /apollo/canbus/chassis      134   
1            0  COMPLETE_MANUAL  /apollo/canbus/chassis      134   
2            0  COMPLETE_MANUAL  /apollo/canbus/chassis      134   
3            0  COMPLETE_MANUAL  /apollo/canbus/chassis      134   
4            0  COMPLETE_MANUAL  /apollo/canbus/chassis      134   
...        ...              ...                     ...      ...   
31898        0  COMPLETE_MANUAL  /apollo/canbus/chassis      134   
31899        0  COMPLETE_MANUAL  /apollo/canbus/chassis      134   
31900        0  COMPLETE_MANUAL  /apollo/canbus/chassis      134   
31901        0  COMPLETE_MANUAL  /apollo/canbus/chassis      134   
31902        0  COMPLETE_MANUAL  /apollo/canbus/chassis      134   

                    time_x  gearLocation  \
0      1692285265243057842  GEAR_PARKING   
1      1692285265274984780  GEAR_PARKING   
2      1692285265313385869  GEAR_PARKING   
3      1692285265341027973  GEAR_PARKING   
4      1692285265376207966  GEAR_PARKING   
...                    ...           ...   
31898  1692287267717287214    GEAR_DRIVE   
31899  1692287267749098870    GEAR_DRIVE   
31900  1692287267783135265    GEAR_DRIVE   
31901  1692287267814949035    GEAR_DRIVE   
31902  1692287267870097127    GEAR_DRIVE   

                                 metadataID  throttlePercentage  \
0      3a2a78cd-db21-11ee-a158-97f8443fd730                 0.0   
1      3a2a78cd-db21-11ee-a158-97f8443fd730                 0.0   
2      3a2a78cd-db21-11ee-a158-97f8443fd730                 0.0   
3      3a2a78cd-db21-11ee-a158-97f8443fd730                 0.0   
4      3a2a78cd-db21-11ee-a158-97f8443fd730                 0.0   
...                                     ...                 ...   
31898  c9760136-db2a-11ee-a158-97f8443fd730                 0.0   
31899  c9760136-db2a-11ee-a158-97f8443fd730                 0.0   
31900  c9760136-db2a-11ee-a158-97f8443fd730                 0.0   
31901  c9760136-db2a-11ee-a158-97f8443fd730                 0.0   
31902  c9760136-db2a-11ee-a158-97f8443fd730                 0.0   

       steeringPercentage  brakePercentage  ... latitudeStdDev  \
0               -6.307542              0.0  ...       0.010128   
1               -6.307542              0.0  ...       0.010128   
2               -6.307542              0.0  ...       0.010128   
3               -6.307542              0.0  ...       0.010128   
4               -6.307542              0.0  ...       0.010128   
...                   ...              ...  ...            ...   
31898            0.714985             26.9  ...       0.009949   
31899            0.714985             26.9  ...       0.009949   
31900            0.714985             26.9  ...       0.009949   
31901            0.714985             26.9  ...       0.009949   
31902            0.714985             26.9  ...       0.009949   

      differentialAge  longitude     solType  solutionAge     solStatus  \
0                 1.0 -82.127926  NARROW_INT          0.0  SOL_COMPUTED   
1                 1.0 -82.127926  NARROW_INT          0.0  SOL_COMPUTED   
2                 1.0 -82.127926  NARROW_INT          0.0  SOL_COMPUTED   
3                 1.0 -82.127926  NARROW_INT          0.0  SOL_COMPUTED   
4                 1.0 -82.127926  NARROW_INT          0.0  SOL_COMPUTED   
...               ...        ...         ...          ...           ...   
31898             1.0 -82.128211  NARROW_INT          0.0  SOL_COMPUTED   
31899             1.0 -82.128211  NARROW_INT          0.0  SOL_COMPUTED   
31900             1.0 -82.128211  NARROW_INT          0.0  SOL_COMPUTED   
31901             1.0 -82.128211  NARROW_INT          0.0  SOL_COMPUTED   
31902             1.0 -82.128211  NARROW_INT          0.0  SOL_COMPUTED   

        latitude  numSatsInSolution LatLonTotalStdDev            time_sec  
0      39.329602                 15          0.014380 2023-08-17 15:14:25  
1      39.

In [283]:
d2_cols = [
    "drivingMode",
    "BinaryDrivingMode",
    "TernaryDrivingModeTransition",
    "time_x",
    "time_sec",
    "speedMps",
    "throttlePercentage",
    "brakePercentage",
    "steeringPercentage",
    "steeringRate",
    "numSatsInSolution",
    "LatLonTotalStdDev",
    "latitude",
    "longitude",
    "differentialAge",
    # "topic_x",
    # "groupMetadataID_x",
    # "signal.turnSignal",
    # "wheelSpeed.wheelSpdRr",
    # "wheelSpeed.wheelSpdFr",
    # "wheelSpeed.wheelSpdRl",
    # "wheelSpeed.wheelSpdFl",
    # "ChassisBestPoseMatchedTime",
    # "topic_y",
    # "gpsGlonassUsedMask",
    "time_y",
    # "longitudeStdDev",
    # "undulation",
    # "numSatsTracked",
    # "baseStationId",
    # "latitudeStdDev",
    # "solType",
    # "galileoBeidouUsedMask",
    # "numSatsL1",
    # "datumId",
    # "measurementTime",
    # "extendedSolutionStatus",
    # "heightStdDev",
    # "numSatsMulti",
    # "heightMsl",
    # "groupMetadataID_y",
    # "solutionAge",
    # "solStatus",
]


r_cols = [
    "BinaryDrivingMode"
    # "TernaryDrivingModeTransition"
]

In [284]:
# Define your map with your dataframe name first and keep everything else the same
fig = px.scatter_mapbox(merged_df, 
                        lat="latitude",
                        lon="longitude",
                        hover_data=["time_x", "time_sec"],
                        #color="drivingMode",
                        zoom=13,
                        height=1000,
                        width=1200,
                        # color_discrete_map={
                        #   "M->A": "#63ACBE",
                        #   "A->M": "#601A4A",
                        #   "ERROR": "#EE442F",
                        #   "NONE":"yellowgreen",
                        # }
                        color_discrete_map={
                            "COMPLETE_MANUAL": "#601A4A",
                            "COMPLETE_AUTO_DRIVE": "#63ACBE",
                            "EMERGENCY_MODE": "#EE442F",
                        }
                        #color_discrete_map={
                        #    "0": "#EE442F",
                        #    "1": "#63ACBE",
                        #}

                        )

# Layout settings
fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})

fig.update_traces(marker=dict(size=8,opacity=0.05))

# Display the map
fig.show()

### Segmentation

In [285]:
#i = merged_df[(merged_df["BinaryDrivingMode"] == 0) & (1 == merged_df.shift()["BinaryDrivingMode"])].index[0]

delta_time = 10000000000 # 10 seconds
#delta_time = 60000000000 # 60 seconds

i = 0

segments = pd.DataFrame()

for t in merged_df[(merged_df["TernaryDrivingModeTransition"] == -1)]["time_y"]:
    #print(t)

    segment =  merged_df[(merged_df["time_y"].between(t-delta_time,t))][d2_cols]
    
    segment["segment_num"] = i
    
    segments = pd.concat([segments, segment])
    i+= 1

segments    

drivingMode  BinaryDrivingMode  TernaryDrivingModeTransition  \
3851   COMPLETE_AUTO_DRIVE                  1                             0   
3852   COMPLETE_AUTO_DRIVE                  1                             0   
3853   COMPLETE_AUTO_DRIVE                  1                             0   
3854   COMPLETE_AUTO_DRIVE                  1                             0   
3855   COMPLETE_AUTO_DRIVE                  1                             0   
...                    ...                ...                           ...   
31185  COMPLETE_AUTO_DRIVE                  1                             0   
31186  COMPLETE_AUTO_DRIVE                  1                             0   
31187  COMPLETE_AUTO_DRIVE                  1                             0   
31188  COMPLETE_AUTO_DRIVE                  1                             0   
31189      COMPLETE_MANUAL                  0                            -1   

                    time_x            time_sec  speedMps  throttlePercentage  \
3851   1692285401570297159 2023-08-17 15:16:41     22.14                17.0   
3852   1692285401603704132 2023-08-17 15:16:41     22.14                17.0   
3853   1692285401631968808 2023-08-17 15:16:41     22.15                17.0   
3854   1692285401666134565 2023-08-17 15:16:41     22.14                17.0   
3855   1692285401697580186 2023-08-17 15:16:41     22.14                16.8   
...                    ...                 ...       ...                 ...   
31185  1692287221658046078 2023-08-17 15:47:01     19.06                 3.9   
31186  1692287221681923644 2023-08-17 15:47:01     19.06                 0.0   
31187  1692287221725117778 2023-08-17 15:47:01     19.07                 0.0   
31188  1692287221747901806 2023-08-17 15:47:01     19.08                 0.0   
31189  1692287221782090734 2023-08-17 15:47:01     19.06                 0.0   

       brakePercentage  steeringPercentage  steeringRate  numSatsInSolution  \
3851               0.0           -0.146915             0                 10   
3852               0.0           -0.127326             0                 10   
3853               0.0           -0.127326             0                 10   
3854               0.0           -0.127326             0                 10   
3855               0.0           -0.127326             0                 10   
...                ...                 ...           ...                ...   
31185              0.0            0.440744             0                 14   
31186              0.0            0.440744             0                 14   
31187              0.0            0.440744             0                 14   
31188              0.0            0.460333             0                 14   
31189              0.0            0.470127             0                 14   

       LatLonTotalStdDev   latitude  longitude  differentialAge  \
3851            0.023940  39.321698 -82.109038              1.0   
3852            0.023940  39.321698 -82.109038              1.0   
3853            0.023940  39.321698 -82.109038              1.0   
3854            0.023940  39.321698 -82.109038              1.0   
3855            0.023940  39.321698 -82.109038              1.0   
...                  ...        ...        ...              ...   
31185           0.017738  39.333567 -82.131870              1.0   
31186           0.017738  39.333567 -82.131870              1.0   
31187           0.017738  39.333567 -82.131870              1.0   
31188           0.017738  39.333567 -82.131870              1.0   
31189           0.017738  39.333567 -82.131870              1.0   

                    time_y  segment_num  
3851   1692285402042981585            0  
3852   1692285402042981585            0  
3853   1692285402042981585            0  
3854   1692285402042981585            0  
3855   1692285402042981585            0  
...                    ...          ...  
31185  1692287221039167013           15  
31186  16922872

In [293]:
# Define your map with your dataframe name first and keep everything else the same
fig = px.scatter_mapbox(segments.drop_duplicates(subset=["latitude", "longitude"]), 
                        lat="latitude",
                        lon="longitude",
                        hover_data=d2_cols + ["segment_num"],
                        color="drivingMode",
                        zoom=13,
                        height=1000,
                        width=1200,
                        opacity=0.5,
                        # color_discrete_map={
                        #   "M->A": "#63ACBE",
                        #   "A->M": "#601A4A",
                        #   "ERROR": "#EE442F",
                        #   "NONE":"yellowgreen",
                        # }
                        color_discrete_map={
                            "COMPLETE_MANUAL": "#601A4A",
                            "COMPLETE_AUTO_DRIVE": "#63ACBE",
                            "EMERGENCY_MODE": "#EE442F",
                        }
                        #color_discrete_map={
                        #    "0": "#EE442F",
                        #    "1": "#63ACBE",
                        #}

                        )

# Layout settings
fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})

fig.update_traces(marker=dict(size=15))#, opacity=0.2))

# Display the map
fig.show()

### Keras

In [46]:
X = merged_df[d2_cols].copy()
y = merged_df[r_cols].copy()

In [48]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=0)

In [ ]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout

# Load data
data = merged_df.copy()

# Create time-lagged sequences
def create_sequences(data, time_steps):
    X, y = [], []
    for i in range(len(data) - time_steps):
        X.append(data[i:i + time_steps])
        y.append(data['disengagement'].iloc[i + time_steps])
    return np.array(X), np.array(y)

# Normalize features
scaler = MinMaxScaler()
data_scaled = scaler.fit_transform(data.drop(columns=['disengagement_label', 'timestamp']))  # Adjust as necessary
data['disengagement'] = data['disengagement_label'].shift(-1)  # Label for disengagement
data.dropna(inplace=True)

# Define time steps (e.g., 50 for 5 seconds at 0.1 second intervals)
time_steps = 50
X, y = create_sequences(data_scaled, time_steps)

# Split data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Reshape X for LSTM (samples, time steps, features)
X_train = X_train.reshape((X_train.shape[0], X_train.shape[1], X_train.shape[2]))
X_test = X_test.reshape((X_test.shape[0], X_test.shape[1], X_test.shape[2]))

# Step 3: Build the LSTM Model
model = Sequential()
model.add(LSTM(50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
model.add(Dropout(0.2))
model.add(LSTM(50, return_sequences=False))
model.add(Dropout(0.2))
model.add(Dense(1, activation='sigmoid'))  # Use 'softmax' for multi-class

# Compile the model
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

# Step 4: Train the Model
model.fit(X_train, y_train, epochs=50, batch_size=32, validation_data=(X_test, y_test))

# Step 5: Evaluate the Model
loss, accuracy = model.evaluate(X_test, y_test)
print(f'Loss: {loss}, Accuracy: {accuracy}')

# Step 6: Predictions
y_pred = model.predict(X_test)
